# Processing data for bridge identification

## Download to your data folder

* Bridges: <a target='_blank' href="https://nyc3.digitaloceanspaces.com/astoria/geo509/data/NBI-220829.gdb.zip">download</a>
* Hydro: <a target='_blank' href="https://apps.nationalmap.gov/downloader/">USGS</a>
* Census: <a target='_blank'  href="https://nyc3.digitaloceanspaces.com/astoria/geo509/data/USCensus-2020.zip">2020 US Census for Kentucky</a>
* Roads: <a target='_blank' href="https://ky.app.box.com/s/vvmznssbbab3cohbco4ef88wzoy8sy7y">Ky Geo Network</a>

Most of these sources are file geodatabases. The road layer is a Shapefile collected into a single folder.

## Set your parameters

In the below cell, set the parameters to match folder names on your local computer and the desired watershed that you want to explore. Watch out for spelling. All strings are case sensitive. This notebook assumes you are working on the C: drive and have already created a Map project in ArcGIS Pro.

In [ ]:
# Set your root GIS folder name
root = 'BoydsGIS'

# Set your project folder name, which was created when you started New Map in ArcGIS Pro.
# Verify the spelling from the of folder names in your root GIS folder. Spelling is case sensitive.
project = 'test'

# Set your folder names for your downloaded data located in your root GIS folder called "data". 
# Geodatabases are folders.

# NHD Hydro
hydro = 'NHDPLUS_H_0510_HU4\\NHDPLUS_H_0510_HU4_GDB.gdb'

# Bridges
bridges = 'NBI-220829.gdb'

# Census
census = 'USCensus-2020\\CensusDemographics2020.gdb'

# Roads 
roads = 'AllRds_M'

#### SET THIS ####
# Which watershed biundary layer are you using? HU12 are the smallest units.
wbd = "WBDHU12" # WBDHU12 or WBDHU10

# What is the EXACT name of the watershed?
wbdName = "Elisha Creek-Red Bird River"

# What do you want to call it?
output = "elisha_creek"

## Processing

If you downloaded the specified data, you should not have to modify the below cells. Run them in sequence from top to bottom. If you select a different watershed, you will need to rerun the entire notebook again.

In [ ]:
# Load all of the tools from ArcGIS Pro
import arcpy
import subprocess

def listContents(root, folder=''):
    """Function to print contents of a directory and report time when the cell finished processing.
    listContents(root, folder)
    Two arguments:
        root = folder for your root GIS space (string)
        folder = path to folder in root (string)
    """
    listcontents = f'c:\\{root}\\{folder}'
    completed = subprocess.run(f'dir {listcontents}', shell=True, stdout=subprocess.PIPE)
    print(completed.stdout.decode('UTF-8'))
    print("Finished processing", datetime.datetime.now())

## Let's see if you have data

Before we process and analysis the data, let's make sure you have data in the folders you made as parameters above.

In [ ]:
# This function will list the contents of the Root GIS folder.
listContents(root)

In [ ]:
# This function will list the contents of the above folder.
listContents(root, project)

## Do you see files and folders in the above list?
If so, let's move on to setting the folder names of your data sources. Use the output from the below cell to verify the folder names in your data folder.

In [ ]:
# This function will list the contents of the above folder.
listContents(root, 'data')

## Let's check the data!
If output in the below cell shows spatial data in these sources, you are good to move on to the next cells. If not, you'll need to set the above data sources to correct names and/or change the folder names in your data directory.

In [ ]:
# Show data in your database
x = [hydro, bridges, census, roads]
    
for i in x:
    name = f'c:\\{root}\\data\\{i}'
    arcpy.env.workspace = name
    l = arcpy.ListFeatureClasses()
    d = arcpy.ListDatasets()
    contents = f'{name} has layers in:\nDatasets: {d}\nFeature Classes: {l}\n'
    print(contents)


## See data?

If you see lists of data, like below, please proceed.

```txt
c:\BoydsGIS\data\NHDPLUS_H_0510_HU4\NHDPLUS_H_0510_HU4_GDB.gdb has layers in:
Datasets: ['NHDPlus', 'WBD', 'Hydrography']
Feature Classes: []

c:\BoydsGIS\data\NBI-220829.gdb has layers in:
Datasets: ['Roads_27']
Feature Classes: []

c:\BoydsGIS\data\USCensus-2020\CensusDemographics2020.gdb has layers in:
Datasets: []
Feature Classes: ['CensusBlocks_2020', 'CensusBlockGroups_2020', 'CensusTracts_2020', 'CensusCounties_2020']

c:\BoydsGIS\data\AllRds_M has layers in:
Datasets: []
Feature Classes: ['AllRds_M.shp']
```

In [ ]:
# Our global variables

# Your geodatabase
arcpy.env.workspace = f"C:\\{root}\\{project}\\{project}.gdb"

# Other geodatabases
watersheds = f"C:\\{root}\\data\\{hydro}\\"
brdgs = f"C:\\{root}\\data\\{bridges}\\Roads_27\\National_Bridge_Inventory_DS_nbi_June_15_2022"
rds = f"C:\\{root}\\data\\{roads}\\AllRds_M.shp"
cens = f"C:\\{root}\\data\\{census}\\CensusBlocks_2020"

# Overwrite any existing output
arcpy.env.overwriteOutput = True

# Create the spatial reference object for Kentucky
sr = arcpy.SpatialReference(3089)
arcpy.env.outputCoordinateSystem = sr


## Extract your watershed

Find your watershed's name, either in the WBDHU12 or WBDHU10 layers

In [ ]:
# Do the selection and export to new layer
arcpy.Select_analysis(f"{watersheds}WBD\\{wbd}", f"{output}_aoi", f"\"Name\" = '{wbdName}'")

# Whoops! We have duplicates!
arcpy.DeleteIdentical_management(f"{output}_aoi", "Name")

## Clip your features to your AOI

Ok, now let's reduce the overhead of extra data. 

In [ ]:
# Clip bridges
arcpy.Clip_analysis(brdgs, f"{output}_aoi", f"{output}_bridges")

# Clip roads
arcpy.Clip_analysis(rds, f"{output}_aoi", f"{output}_roads")

# Clip streams
arcpy.Clip_analysis(f"{watersheds}Hydrography\\NHDFlowline", f"{output}_aoi", f"{output}_strms")

# Clip lakes
arcpy.Clip_analysis(f"{watersheds}Hydrography\\NHDWaterbody", f"{output}_aoi", f"{output}_lakes")

# Clip large streams
arcpy.Clip_analysis(f"{watersheds}Hydrography\\NHDArea", f"{output}_aoi", f"{output}_strms_lg")

# Clip census blocks
arcpy.Clip_analysis(cens, f"{output}_aoi", f"{output}_census")

## Extract your AOI from raster layers

Watch out! These cells could take some time to run. 

In [ ]:
# Show data in your database
yourLayers = arcpy.ListRasters()
yourLayers

In [ ]:
# Get digital surface model
source = 'https://kyraster.ky.gov/arcgis/rest/services/ElevationServices/Ky_DSM_First_Return_5FT_Phase1/ImageServer'
first_return = arcpy.sa.Raster(source)

# Verify
first_return

In [ ]:
arcpy.Clip_management(
    source,"#",
    f"{output}_dsm", f"{output}_aoi", "#", True, "NO_MAINTAIN_EXTENT")

## Analysis

Let's create some layers to help identify bridges.

In [ ]:
# Hillshade the DSM to help visualize features
arcpy.HillShade_3d(f"{output}_dsm", f"{output}_hillshade")

In [ ]:
# Intersect roads and streams to spot potential bridges
inFeatures = [f"{output}_roads", f"{output}_strms"]
arcpy.Intersect_analysis(inFeatures, f"{output}_potential_brig", "#", "#", "Point")

## All done!

In [ ]:
# wbd = 'wbdhu12_prj'
# with arcpy.da.SearchCursor(wbd,['SHAPE@', 'Name']) as cursor:
#     for row in cursor:
#         print(row[1][:3])
#         a = arcpy.sa.ExtractByMask(first_return, row[0])
#         a.save(f'DSM_{row[1][:3]}')
        